# Math 124 - Programming for Mathematical Applications
Per-Olof Persson, UC Berkeley

## Project 5 - Deep Neural Networks

In this project, you will implement a **Deep Neural Network** from scratch to solve a non-linear binary classification problem. The goal is to demystify the "black box" of deep learning by manually implementing the **backpropagation** algorithm.

We will test the network on a geometric classification problem: recognizing a specific shape (a "Pac-Man" figure). We will observe how increasing the depth and width of the network architecture allows it to model complex, non-convex boundaries.

In [ ]:
using LinearAlgebra, Plots

### Preliminaries: The Deep Network

We will implement a fully connected neural network with $L$ layers.

**Notation:**
- **Input:** $a^0 = x$ (a vector of size 2).
- **Parameters:** For layer $l$, we have a weight matrix $W^l$ and a bias vector $b^l$.
- **Pre-activation:** $z^l = W^l a^{l-1} + b^l$. This is the linear transformation of the previous layer's output.
- **Activation:** $a^l = \phi(z^l)$. This is the non-linear output of layer $l$.

**Architecture:**
1.  **Hidden Layers:** Use the **ReLU** activation function: $\phi(z) = \max(0, z)$. This introduces non-linearity, allowing the network to learn complex shapes.
2.  **Output Layer:** Use the **Sigmoid** activation function $\sigma(z) = \frac{1}{1 + e^{-z}}$. This squashes the output to the range $(0, 1)$, representing a probability $\hat{y} = a^L$.

**Loss Function:**
Since this is a binary classification problem (determining if a point is "Inside" vs "Outside"), we use the **Binary Cross Entropy** loss. For a single training example with target $y \in \{0, 1\}$ and prediction $a^L$:
$$ E = -y \log(a^L) - (1-y) \log(1 - a^L) $$

**Example Network:** The structure below illustrates a network with $L=3$ layers and widths $[2, 6, 3, 1]$.

### Training via Backpropagation

We will train the network using **Stochastic Gradient Descent (SGD)**. In each iteration, we sample a random point $x$, compare the prediction to the true label $y$, and update the weights to minimize the error.

**The Backpropagation Algorithm:**

To update weights, we need the gradient of the loss. We define the error term $\delta^l$ as the gradient of the loss with respect to the pre-activation: $\delta^l \equiv \frac{\partial E}{\partial z^l}$.

1.  **Forward Pass:** Compute and store $z^l$ (pre-activations) and $a^l$ (activations) for all layers $l=1 \dots L$.
2.  **Output Error:** Compute $\delta^L$ for the last layer. By the Chain Rule, $\delta^L = \frac{\partial E}{\partial a^L} \cdot \sigma'(z^L)$. Due to the convenient cancellation between the derivative of the Sigmoid and the Log-Loss, this simplifies to:
    $$\delta^L = a^L - y$$
3.  **Backward Pass:** For $l = L-1, \dots, 1$, propagate the error backwards.
    The error $\delta^{l+1}$ flows back through the transpose of the weights $(W^{l+1})^T$. We then multiply by the local derivative of the activation function, $\phi'(z^l)$. Since $\phi$ operates element-wise, this is an element-wise multiplication (denoted by $\odot$):
    $$\delta^l = ((W^{l+1})^T \delta^{l+1}) \odot \phi'(z^l)$$
4.  **Compute Gradients:** Use $\delta^l$ to find the gradients with respect to the parameters.
    Because $z^l = W^l a^{l-1} + b^l$, the gradients are:
    $$\frac{\partial E}{\partial W^l} = \delta^l (a^{l-1})^T, \quad \frac{\partial E}{\partial b^l} = \delta^l$$
5.  **Update Parameters:** $W^l \leftarrow W^l - \eta \frac{\partial E}{\partial W^l}$, and similarly for $b^l$.

---

### Problem 1: Building Blocks

#### Problem 1a.

Implement the scalar activation functions:
1. `relu(x)`: Return $\max(0, x)$.
2. `relu_prime(x)`: The derivative. Return $1$ if $x > 0$, else $0$.
3. `sigmoid(x)`: Return $\frac{1}{1 + e^{-x}}$.

In [ ]:
relu(x) = # TODO
relu_prime(x) = # TODO
sigmoid(x) = # TODO

In [ ]:
# Test your functions by plotting them for -3 <= x <= 3
xx = -3:0.01:3
plot(xx, [relu.(xx) relu_prime.(xx) sigmoid.(xx)],
    labels=["ReLU" "ReLu'" "σ"],
    aspect_ratio=:equal,
    title="Activation Functions")

#### Problem 1b.

Implement `init_network(layer_dims)`, where `layer_dims` is a vector of layer sizes (e.g., `[2, 8, 4, 1]`). This function should return two vectors of arrays: `Ws = [W1, W2, ..., WL]` and `bs = [b1, b2, ..., bL]`.

* **Note:** The number of layers is `L = length(layer_dims) - 1`.
* **Weights:** Use random normal values for each $W$, multiplied by $\sqrt{2/n_{in}}$ where $n_{in}$ is the number of input neurons (columns) of $W$. This is known as **He initialization** and helps maintain signal variance through deep networks.
* **Biases:** Initialize each bias $b$ to a vector of zeros.

In [ ]:
function init_network(layer_dims)
    L = length(layer_dims) - 1

    # TODO
    
    return Ws, bs
end

In [ ]:
# Test by computing `Ws, bs` for `layer_dims = [2,8,4,1]` and confirm all array sizes are correct
Ws, bs = init_network([2,8,4,1])
@show size.(Ws);
@show size.(bs);

#### Problem 1c.

Implement `network_forward(x, Ws, bs)`. 

This function performs a **forward pass** only and returns the final probability output. It is used for making predictions and does not need to store intermediate values.

In [ ]:
function network_forward(x, Ws, bs)
    # TODO
end

In [ ]:
# Test by computing the output of the network Ws, bs at the coordinate x = [0.,0.]
network_forward([0.,0.], Ws, bs)

#### Problem 1d.

For backpropagation, we need access to all intermediate activations $a^l$ and pre-activations $z^l$. 

Implement `network_forward_output_all(x, Ws, bs)`. This performs a **forward pass** and returns two vectors, `as` and `zs`, containing all activations and pre-activations respectively.

* `as` should contain $[a^0, a^1, \dots, a^L]$
* `zs` should contain $[z^1, z^2, \dots, z^L]$

In [ ]:
function network_forward_output_all(x, Ws, bs)
    # as = [ a^0, a^1, ..., a^L ]
    # zs = [ z^1, z^2, ..., z^L ]

    # TODO

    return as, zs
end

In [ ]:
# Test by computing (as, zs) for the network Ws, bs and x = [0.,0.]
# Check that all array sizes are as expected
as, zs = network_forward_output_all([0.,0.], Ws, bs)
@show size.(as);
@show size.(zs);

#### Problem 1e.

Implement a function `network_gradient(x, y, Ws, bs)`. This is the core engine of our training.

1. Run `network_forward_output_all` to get the current state.
2. Use the **Backpropagation Algorithm** described above to compute the gradients of the loss with respect to every weight and bias.
3. Return the gradients in vectors `grad_Ws` and `grad_bs` (which should match the structure of `Ws` and `bs`).

In [ ]:
function network_gradient(x, y, Ws, bs)
    L = length(Ws)
    
    # TODO
    
    return grad_Ws, grad_bs
end

In [ ]:
# Test by computing the gradient for the network Ws, bs, at the coordinates x = [0.,0.] and y = [0.0]
# Check that all array sizes are as expected
grad_Ws, grad_bs = network_gradient([0.0,0.0], [0.0], Ws, bs)
@show size.(grad_Ws);
@show size.(grad_bs);

---

## Problem 2: Training with Stochastic Gradient Descent

Implement `train_descent(is_inside_func, layer_dims, eta, n_iter)`.

**Parameters:**
* `is_inside_func`: A function that returns `true`/`false` for a given input $x$.
* `layer_dims`: Vector of layer sizes.
* `eta`: Learning rate (step size).
* `n_iter`: Total number of SGD iterations.

**The Training Loop:**
1. Initialize `Ws, bs` using `init_network`.
2. Loop for `n_iter` iterations.
3. In each iteration, generate a random sample $x$ uniformly from $[-1.2, 1.2]^2$.
4. Determine the true label `y_true`: $1.0$ if inside, $0.0$ if outside.
5. Compute gradients and update weights/biases using the gradient descent update rule ($\text{param} \leftarrow \text{param} - \eta \cdot \text{gradient}$).
6. Return the trained `Ws, bs`.

In [ ]:
function train_descent(is_inside_func, layer_dims, eta, n_iter)

    # TODO
    
    return Ws, bs
end

---

### Problem 3: Analysis

We will now test our network on a "Pac-Man" shape (a circle with a wedge removed). This shape is **non-convex**, making it a challenging boundary for simple linear classifiers.

Run the training for `100,000` iterations with a learning rate `eta = 0.02` for the following architectures:

1.  **Shallow & Small:** `[2, 8, 1]` (One hidden layer, 8 neurons). Low capacity.
2.  **Shallow & Wide:** `[2, 64, 1]` (One hidden layer, 64 neurons). High capacity, but shallow.
3.  **Deep & Structured:** `[2, 8, 8, 1]` (Two hidden layers, 8 neurons each). Deep, structured capacity.

**Tasks:**
1. Train each model.
2. Plot the resulting decision boundary.
3. Calculate and print the total number of trainable parameters for each model.

**Discussion:** Compare the results. Which networks succeeded in capturing the "wedge"? How does the parameter count of the Deep model compare to the Wide model?

In [ ]:
# Helper: The True Geometry (Pac-Man shape)
function pacman_inside(x)
    in_circle = (x[1]^2 + x[2]^2 < 0.8^2)
    in_wedge = (x[1] > 0) && (abs(x[2]) < x[1] * tan(pi/6))
    return in_circle && !in_wedge
end

# Helper: Plotting the Decision Boundary
function plot_decision_boundary(Ws, bs, title_text)
    xs = range(-1.2, 1.2, length=100)
    ys = range(-1.2, 1.2, length=100)
    
    # Evaluate network on a 100x100 grid
    Z = [network_forward([x, y], Ws, bs)[1] for y in ys, x in xs]
    
    # Plot heatmap of prediction probability
    p = heatmap(xs, ys, Z, c=:RdBu, clims=(0,1), title=title_text,
        aspect_ratio=:equal, axis=nothing, border=:none, colorbar=false)
    
    # Overlay the true boundary line for comparison
    true_Z = [pacman_inside((x,y)) ? 1.0 : 0.0 for y in ys, x in xs]
    contour!(p, xs, ys, true_Z, levels=[0.5], c=:black, lw=2)
    return p
end

In [ ]:
plts = []
for layer_dims = [[2, 8, 1],
                  [2, 64, 1],
                  [2, 8, 8, 1]]
                  
    println("Training architecture: ", layer_dims)

    # TODO: Train a network Ws, bs
    
    plt = plot_decision_boundary(Ws, bs, layer_dims)
    push!(plts, plt)
    
    # Count total parameters (elements in all W matrices + elements in all b vectors)

    n_params = # TODO: Compute the total number of parameters in the network Ws, bs

    println("   -> Total parameters: ", n_params)
end

plot(plts..., layout = (1,3), size=(800,300))

**Discussion of Results:**

*TODO: Write a brief summary of your observations*